# Top 10 most frequent people

In [22]:
import data
import pandas as pd
import csv
import networkx as nx
import plotly.express as px
import datetime
import json

journal = "FRANCE_SN"


## HIST TOP 10

In [23]:
dfDictPers = pd.read_csv(f"../PeopleSaves/{journal}_DictPers.csv")
dictPers = dfDictPers.set_index('Names').to_dict()["Values"]
print(dictPers)
histdict = {}

#Modèle pour le barchart se trouvant dans le dashboard.py 
for name,value in dictPers.items():

    if len(histdict)<10:
        histdict[name] = value
    else:
        min_key = min(histdict, key=histdict.get)
        min_value = min(histdict.values())
        if value > min_value:
            del histdict[min_key]
            histdict[name] = value
    
names = list(histdict.keys())
values = list(histdict.values())
hist_df = pd.DataFrame({'Names':names,'Values': values})    


hist_df.to_csv(f"..//PeopleSaves/{journal}_Top10_People.csv")
fig = px.bar(hist_df, x='Names', y='Values', labels={'Names': 'Nom', 'Values': 'Valeur'}, title='Histogramme des 10 personnes les plus fréquentes')

fig.show()
    

{'darmanin': 559, 'paty': 982, 'estrosi': 160, 'castex': 57, 'macron': 4968, 'fouche': 50, 'sihamedi': 5, 'erdogan': 465, 'mediapart': 2, 'marianne': 255, 'boutin': 1012, 'mahomet': 198, 'darmagnac': 22, 'conte': 219, 'vardon': 248, 'clair': 131, 'sarkozy': 243, 'ghali': 135, 'derrar': 55, 'hamlat': 69, 'cherif': 46, 'ramdane': 62, 'ouane': 118, 'chaliand': 33, 'hassen': 188, 'hodcroft': 2, 'hirsch': 29, 'covid': 100, 'attal': 264, 'toussaint': 13, 'hollande': 169, 'cohen': 66, 'ikken': 7, 'gallois': 51, 'praud': 148, 'piot': 375, 'tikhanovskaia': 18, 'washington': 367, 'tagne': 299, 'jong': 208, 'balanant': 3, 'martinez': 43, 'nasrallah': 17, 'pomart': 23, 'blanquer': 163, 'villiers': 99, 'mamoun': 140, 'dupuy': 180, 'luca': 125, 'drian': 370, 'chergui': 8, 'guterrez': 25, 'ciotti': 87, 'mohamad': 41, 'noroozia': 2, 'noroozile': 2, 'aydalot': 2, 'reuters': 2, 'majid': 134, 'tolstoi': 4, 'philippe': 528, 'blanc': 70, 'sadouni': 17, 'thomson': 10, 'potier': 108, 'turc': 205, 'masbah': 9

## Evolution with time TOP 10

In [24]:
top10 = [key for key in histdict.keys()]
print(top10)
LIMITE = 4
arts = data.open_file(data.get_data(journal))["data-all"]
date_article = {}
for year in sorted(arts):
        
    for month in sorted(arts[year]):
            
        for day in sorted(arts[year][month]):
            for art,i in enumerate(arts[year][month][day]):
                pers_list = arts[year][month][day][art]["per"]
                date =datetime.datetime(int(year),int(month),int(day))
                if date in date_article.keys():
                    
                    date_article[date].append(pers_list)
                else:
                    date_article[date]= [pers_list]
                
print(date_article)
   
                    
date_article = {k: date_article[k] for k in sorted(date_article)}

top10_dict = {}
for pers in top10:
    sigma = 0
    temporary_list = []
    for date, liste in date_article.items():
        for list_per in liste:
            normalized_names = {data.normalize_name(key):value for key,value in list_per.items()}
            print(normalized_names)
            for normalize_name,value in normalized_names.items():
                if data.same_name(normalize_name,pers,LIMITE):
                    sigma = sigma + normalized_names[normalize_name]
                    temporary_list.append({date.strftime("%Y-%m-%d"):sigma})
    
    top10_dict[pers] = temporary_list
print(top10_dict)

print(len(top10_dict))




#cette partie est également le modèle permettant de réaliser le linechart mettant en avant l'évolution de l'apparition des 10 personnes au cours du temps 

with open(f"../PeopleSaves/{journal}_Top10_People_Evolution.json",'w') as f:
    json.dump(top10_dict,f)
    

fig = None
for key, values in top10_dict.items():
    dates = []
    values_list = []
    for entry in values:
        for date, value in entry.items():
            dates.append(date)
            values_list.append(value)
    if fig is None:
        fig = px.line(labels={'x': 'Date', 'y': 'Valeur'}, title='Evolution de la présence')
        fig.add_scatter(x=dates, y=values_list, mode='lines', name=key)
    else:
        fig.add_scatter(x=dates, y=values_list, mode='lines', name=key)

# Affichage du graphique
fig.show()


['darmanin', 'paty', 'macron', 'boutin', 'philippe', 'maire', 'trump', 'melenchon', 'zemmour', 'haftar']
{datetime.datetime(2018, 12, 31, 0, 0): [{'Denis Tribaudeau': 8, 'Denis TribaudeauDenis TribaudeauDenis': 2}, {}, {'Père Andreï': 7, 'Père Andrei': 2, 'Père Dimitri': 7, 'Serguei Averintsev': 2}, {'Pedro Agramunt': 8, 'Soros': 4, 'George Soros': 9, 'Gérald Knaus': 3, 'Olga Zakharova': 2, 'Yuri Dzhibladze': 2}, {'Sylvie Matelly': 5, 'Nouriel Roubini': 7, 'Donald Trump': 4, 'Philippe Béchade': 6}, {'Emmanuel Macron': 3}, {}, {'Jean-Luc Mélenchon': 3, 'Éric Drouet': 4, 'Drouet': 3, 'Jean-Baptiste Drouet': 2}, {'Michel Houellebecq': 4}, {'Emmanuel Macron': 3, 'Président': 2, 'Macron': 11}, {}, {'Merci': 2, 'bravo': 2}, {}, {}, {}], datetime.datetime(2019, 1, 1, 0, 0): [{'Alexandre Benalla': 3, 'Emmanuel Macron': 5, 'Président de la République': 2, 'Benalla': 5, 'Macron': 6}, {}, {}, {}, {}, {}, {'Donald Trump': 2, 'Jean-Yves le Drian': 2, 'Meyer Habib': 2}, {'Jean-Pierre Duthion': 6, 'M